# Domestic Load Research Programme Customer Class Inference

**Setup instructions**

1. Install libpgm with `pip install libpgm`
2. Execute `2to3 -w /home/user/anaconda3/lib/python3.5/site-packages/utils/bntextutils.py` from the command prompt

## Support functions for BN construction and inference

In [1]:
#load support functions
from classmod.bncore import inferCustomerClasses, classes2csv
from classmod.bnevidence import generateEvidenceExp1, saveEvidence
from math import ceil

#initiate offline plotting for plotly
import plotly.offline as offline
import plotly.graph_objs as go
from plotly import tools
offline.init_notebook_mode(connected=True)

#set data directory that contains evidence
model = 'exp1_bn.txt'
evidence_dir = 'exp1'

## BN Evidence

### Generate evidence set for the customer class model.

In [2]:
for year in range(2000, 2015):
    evidence, year = generateEvidenceExp1(year)
    saveEvidence(evidence, year, experiment_dir = 'exp1')

Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2000.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2001.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2002.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2003.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2004.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2005.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2006.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2007.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2008.txt
Successfully saved to /home/saintlyvi/git/DLR/DLR_DB/classmod/evidence/exp1/bn_evidence_2009.txt
Successfully saved to /home/sa

## BN Inference

### Generate probability distribution over customer_class variable | evidence

In [3]:
cc12, bn12 = inferCustomerClasses(model, evidence_dir, 2000)
print(cc12.head())
len(cc12)

                 rural       village  informal_settlement  township  \
AnswerID                                                              
1014               NaN           NaN                  NaN       NaN   
89                 NaN           NaN                  NaN       NaN   
1230               NaN           NaN                  NaN       NaN   
696                NaN           NaN                  NaN       NaN   
197       6.617545e-20  8.068189e-17         1.418257e-14  0.000257   

          urban_res_7  urban_townhouse_7-8  urban_res_8-9  \
AnswerID                                                    
1014              NaN                  NaN            NaN   
89                NaN                  NaN            NaN   
1230              NaN                  NaN            NaN   
696               NaN                  NaN            NaN   
197          0.123945             0.050764        0.54059   

          urban_townhouse_9-10  urban_estate_10+  
AnswerID               

988

### Visualise inferred customer classes

In [4]:
def plotClassDist(model, evidence_dir, year):
    """
    This function plots the probability distribution over all the inferred classes for all the AnswerIDs 
    in a given year.
    """
    
    df, bn = inferCustomerClasses(model, evidence_dir, year)
    trace = go.Heatmap(z=df.values.tolist(),
                       x=df.columns,
                       colorscale = 'Viridis')
     
    data=[trace]
    layout = go.Layout(title='Probability Distribution of Customer Classes for ' + str(year))
    
    return offline.iplot({"data":data, "layout":layout})

def plotClassYearRange(yearstart, yearend, model, evidence_dir, col = 2):
    """
    This function creates subplots of the probability distribution over all the inferred classes 
    for a range of years.
    """
    
    ncol = float(col)
    nrow = int(ceil((yearend + 1 - yearstart)/ncol))
   
    fig = tools.make_subplots(rows=nrow, cols=int(ncol), subplot_titles=list(range(yearstart, yearend + 1)), print_grid=False)
    
    r = 1
    c = 1
        
    for y in range(yearstart, yearend + 1):
        count = 1
        if c == ncol + 1: 
            c = 1
        ro = int(ceil(r/ncol))
        
        try:
            df, bn = inferCustomerClasses(model, evidence_dir, y)
            df.columns = list(range(1, df.shape[1] + 1))
            trace = go.Heatmap(z=df.values.tolist(),
                               x=df.columns,
                               colorscale = 'Viridis')
            fig.append_trace(trace, ro, c)
            
        except:
            pass
        
        c += 1
        r += 1
        count += 1

    fig['layout'].update(showlegend=False, title='Probability Distribution of Customer Classes', height=nrow*275)
    
    return offline.iplot(fig)

In [5]:
plotClassDist(model, evidence_dir, 2000)

In [6]:
plotClassYearRange(2000, 2014, model, evidence_dir, col=4)

## Save classes to csv file

In [13]:
for year in range(2000, 2015):
    print(year)
    df, bn = inferCustomerClasses(model, evidence_dir, year)
    filename = 'classes_' + str(year) + '.csv'
    classes2csv(df, filename, out_dir = evidence_dir)

2000
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2000.csv
2001
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2001.csv
2002
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2002.csv
2003
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2003.csv
2004
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2004.csv
2005
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2005.csv
2006
Successfully saved to/home/saintlyvi/git/DLR/DLR_DB/classmod/out/exp1/classes_2006.csv
2007


TypeError: reduction operation 'argmax' not allowed for this dtype